In [1]:
!pip install -e /Users/olgafilippova/work/evidently

Obtaining file:///Users/olgafilippova/work/evidently
  Attempting uninstall: evidently
    Found existing installation: evidently 0.1.40.dev0
    Uninstalling evidently-0.1.40.dev0:
      Successfully uninstalled evidently-0.1.40.dev0
  Running setup.py develop for evidently


In [47]:
import pandas as pd
import numpy as np
from sklearn.datasets import fetch_openml
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
import seaborn as sns

import pandas as pd


from evidently.legacy.dashboard import Dashboard
from evidently.legacy.pipeline.column_mapping import ColumnMapping
from evidently.legacy.dashboard.tabs import ProbClassificationPerformanceTab

from evidently.legacy.model_profile import Profile
from evidently.legacy.model_profile.sections import ProbClassificationPerformanceProfileSection

# Load data

In [81]:
wine = fetch_openml(name='wine_quality', version=1)

In [82]:
wine_df = wine.frame

In [83]:
red = wine_df[:1599]
white = wine_df[1599:]

In [84]:
wine_column_mapping = ColumnMapping()
wine_column_mapping.numerical_features = wine.feature_names

In [86]:
from evidently.legacy.dashboard.tabs import DataDriftTab

In [ ]:
model_performance_dashboard = Dashboard(tabs=[DataDriftTab()])
model_performance_dashboard.calculate(red.sample(1000, random_state=0), 
                                      white.sample(1000, random_state=0), 
                                      column_mapping=wine_column_mapping)
model_performance_dashboard.show()

In [57]:
default_df['y'] = default_df['y'].astype(int)

# Train model, get predictions

In [162]:
wine_df['target'] = (wine_df['quality'] > 5).astype(int)

In [163]:
train_data, test_data = train_test_split(wine_df, random_state=0)

In [164]:
model = LogisticRegression()

In [165]:
model.fit(wine_df[wine.feature_names], wine_df.target)

/Users/olgafilippova/opt/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning:

lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression



LogisticRegression()

In [169]:
train_probas = pd.DataFrame(model.predict_proba(train_data[wine.feature_names]))
train_probas.columns = ['bad', 'good']
test_probas = pd.DataFrame(model.predict_proba(test_data[wine.feature_names]))
test_probas.columns = ['bad', 'good']

In [170]:
train_data['target'] = train_data['target'].map({1: 'good', 0: 'bad'}).astype(str).values
test_data['target'] = test_data['target'].map({1: 'good', 0: 'bad'}).astype(str).values

In [172]:
train_data.reset_index(inplace=True, drop=True)
test_data.reset_index(inplace=True, drop=True)

merged_train_data = pd.concat([train_data, train_probas], axis=1)
merged_test_data = pd.concat([test_data, test_probas], axis=1)

# Probabilistic Model Performance Dashboard full 

In [158]:
wine_column_mapping = ColumnMapping()

wine_column_mapping.target = 'target'
wine_column_mapping.prediction = ['good', 'bad']
wine_column_mapping.numerical_features = wine.feature_names

In [184]:
wine_model_performance_dashboard = Dashboard(tabs=[ProbClassificationPerformanceTab(verbose_level=1)])
wine_model_performance_dashboard.calculate(merged_train_data.sample(1000, random_state=0), 
                                           merged_test_data.sample(1000, random_state=0), 
                                              column_mapping = wine_column_mapping)
wine_model_performance_dashboard.show()

In [181]:
from evidently.legacy.options import QualityMetricsOptions

In [185]:
m_options = QualityMetricsOptions(cut_quantile={'chlorides': ('right', 0.95), 'MedHouseVal': ('right', 0.5)}, 
                                  classification_threshold = 0.8,
                                  conf_interval_n_sigmas=3)

In [186]:
wine_model_performance_dashboard = Dashboard(tabs=[ProbClassificationPerformanceTab(verbose_level=1)],
                                             options=[m_options])
wine_model_performance_dashboard.calculate(merged_train_data.sample(1000, random_state=0), 
                                           merged_test_data.sample(1000, random_state=0), 
                                              column_mapping = wine_column_mapping)
wine_model_performance_dashboard.show()

In [202]:
from evidently.legacy.dashboard.tabs import DataDriftTab

In [203]:
model_performance_dashboard = Dashboard(tabs=[DataDriftTab()], options=[m_options])
model_performance_dashboard.calculate(merged_train_data.sample(1000, random_state=0), 
                                      merged_test_data.sample(1000, random_state=0),
                                      column_mapping=wine_column_mapping)
model_performance_dashboard.show()